# aT 농산품 예측 base line

&nbsp;

## 모듈 가져오기

In [ ]:
# !pip install pandasql

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Created wheel for pandasql: filename=pandasql-0.7.3-py3-none-any.whl size=26784 sha256=22d7ce7358a2edfb01f9e1870d795fc096973cfe6112771f02df5c8b2731371b
  Stored in directory: /root/.cache/pip/wheels/5c/4b/ec/41f4e116c8053c3654e2c2a47c62b4fca34cc67ef7b55deb7f
Successfully built pandasql


In [1]:
import pandas as pd
import numpy as np
from tqdm import tqdm
import random
import warnings
from glob import glob
import tensorflow as tf
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint
from tensorflow import keras
from tensorflow.keras import layers
from sklearn.model_selection import train_test_split
from pandasql import sqldf
import os


# 경고 끄기
warnings.filterwarnings(action='ignore')

# 시드고정
tf.random.set_seed(1215)
random.seed(1215)
np.random.seed(1215)

&nbsp;

## 전처리 Class

In [2]:
class preprocessing_data(object):

    """
    도매, 소매, 수입수출, 도매경락, 주산지 데이터 전처리용 class
    중간결과물 저장 check parameter을 통해 지정, 중간결과물 저장 없이 사용은 check = 0
    """

    def __init__(self,dir):
        """
        전체 데이터에서 해당하는 domae,imexport,pummok,somae,weather 별 분리
        """
        self.data_list = glob(dir)
        self.domae = []
        self.imexport = []
        self.pummok = []
        self.somae = []
        self.weather = []


        for i in self.data_list:
            if 'domae' in i:
                self.domae.append(i)
            if 'imexport' in i:
                self.imexport.append(i)
            if 'pummok' in i.split('/')[-1]:
                self.pummok.append(i)
            if 'somae' in i:
                self.somae.append(i)
            if 'weather' in i:
                self.weather.append(i)


    def add_pummock(self,check=0):

        """
        check = 중간 산출물을 저장하고 싶다면 check 을 0 이외의 숫자로
        pummock의 데이터를 가져와 '해당일자_전체거래물량', '하위가격 평균가', '상위가격 평균가', '하위가격 거래물량', '상위가격 거래물량' 의 파생변수를 생성하는 단계
        """

        for num in tqdm(self.pummok):
            ddf = pd.read_csv(num)  # pummock의 csv 읽어오기
            name = num.split('/')[-1] # 전체 정제한 데이터를 담을 변수 이름

            sep2 = sqldf(f"select *, sum(거래량) as '해당일자_전체거래물량(kg)' from ddf group by datadate")
            # sql 문법을 이용해 '해당일자_전체거래물량' 계산

            height_set = []
            low_set = []
            height_volume_set = []
            low_volume_set = []

            for i in sep2['datadate']:

                """
                sep2는 group by를 통해 각 일자가 합쳐진 상태 예를 들어 '201703' 이 5개 이렇게 있을때 sep2는 group 시켜서 '해당일자_전체거래물량'을 계산
                이후 sep2 기준 20170101 and 20220630 사이의 날짜들에 해당하는 각 '201703' 마다 '해당일자_전체평균가격' 보다 큰지 아니면 작은지 판단
                위 과정을 통해 '하위가격 평균가', '상위가격 평균가', '하위가격 거래물량', '상위가격 거래물량' 변수 생성
                """

                new_list = ddf.loc[[d for d, x in enumerate(ddf['datadate']) if x == i]]
                set_price = sep2.loc[list(sep2['datadate']).index(i)]['해당일자_전체평균가격(원)']

                sum_he_as = sum(new_list['거래대금(원)'].iloc[n] for n, z in enumerate(new_list['단가(원)']) if z >= set_price)
                sum_he_vo = sum(new_list['거래량'].iloc[n] for n, z in enumerate(new_list['단가(원)']) if z >= set_price)

                sum_lo_as = sum(new_list['거래대금(원)'].iloc[n] for n, z in enumerate(new_list['단가(원)']) if z < set_price)
                sum_lo_vo = sum(new_list['거래량'].iloc[n] for n, z in enumerate(new_list['단가(원)']) if z < set_price)

                if sum_lo_vo != 0:
                    low_set.append(sum_lo_as / sum_lo_vo)
                    low_volume_set.append(sum_lo_vo)
                else:
                    low_set.append(np.nan)
                    low_volume_set.append(np.nan)

                if sum_he_vo != 0:
                    height_set.append(sum_he_as / sum_he_vo)
                    height_volume_set.append(sum_he_vo)
                else:
                    height_set.append(np.nan)
                    height_volume_set.append(np.nan)

            sep2['하위가격 평균가(원)'] = low_set
            sep2['상위가격 평균가(원)'] = height_set

            sep2['하위가격 거래물량(kg)'] = low_volume_set
            sep2['상위가격 거래물량(kg)'] = height_volume_set


            globals()[f'df_{name.split("_")[1].split(".")[0]}'] = sep2.copy()


            # 중간 산출물 저장
            if check != 0:
                if os.path.exists(f'./data') == False:
                    os.mkdir(f'./data')

                if os.path.exists(f'./data/품목') == False:
                    os.mkdir(f'./data/품목')

                sep2.to_csv(f'./data/품목/{name}', index=False)




    def add_dosomae(self, option=1, check=0):

        """
        check = 중간 산출물을 저장하고 싶다면 check 을 0 이외의 숫자로
        domae, somae 데이터를 가져와서 정제하는 단계
        option parameter을 통한 도매, 소매 선택
        """

        if option == 1:
            df = self.domae
            text = '도매'
        else:
            df = self.somae
            text = '소매'

        for i in tqdm(df):
            test = pd.read_csv(i)
            name = i.split('/')[-1]

            sep = test.loc[(test['등급명'] == '상품') | (test['등급명'] == 'S과')]  # 모든 상품에 대해서 수행하지 않고 GRAD_NM이 '상품', 'S과' 만 해당하는 품목 가져옴
            sep = sep[['datadate', '등급명', '조사단위(kg)', '가격(원)']]

            sep.rename(columns={"가격(원)": "가격"}, inplace=True)

            sep2 = sqldf(
                f"select datadate, max(가격) as '일자별_{text}가격_최대(원)', avg(가격) as '일자별_{text}가격_평균(원)', min(가격) as '일자별_{text}가격_최소(원)' from sep group by datadate")

            globals()[f'df_{name.split("_")[1].split(".")[0]}'] = globals()[f'df_{name.split("_")[1].split(".")[0]}'].merge(sep2, how='left')

            # 중간 산출물 저장
            if check != 0:
                if os.path.exists(f'./data') == False:
                    os.mkdir(f'./data')

                if os.path.exists(f'./data/{text}') == False:
                    os.mkdir(f'./data/{text}')

                sep2.to_csv(f'./data/{text}/{name}', index=False)

    def add_imexport(self,check=0):
        """
        check = 중간 산출물을 저장하고 싶다면 check 을 0 이외의 숫자로
        imexport 데이터 관련 정제, imexport 데이터는 월별 수입수출 데이터임으로 해당 월에 같은 값을 넣어주고 없는 것에는 np.nan
        해당 품목에 대한 imexport 데이터가 없는 경우 np.nan으로 대체, 모든 품목의 데이터가 동일한 컬럼수를 가지기 위해 수행
        """

        imex_cd = [i.split('_')[-1].split('.')[0] for i in self.imexport]

        for i in tqdm(range(len(self.pummok))):

            cd_number = self.pummok[i].split('_')[-1].split('.')[0]
            file_name = 'imexport_' + self.pummok[i].split('pummok_')[1]


            if cd_number in imex_cd:
                test4 = pd.read_csv(self.imexport[imex_cd.index(cd_number)])

                new_exim1 = []
                new_exim2 = []
                new_exim3 = []
                new_exim4 = []
                new_exim5 = []

                for j in globals()[f'df_{cd_number}']['datadate']:
                    target = j//100

                    try:
                        number = list(test4['datadate']).index(target)


                        new_exim1.append(test4['수출중량(kg)'].iloc[number])
                        new_exim2.append(test4['수출금액(달러)'].iloc[number])
                        new_exim3.append(test4['수입중량(kg)'].iloc[number])
                        new_exim4.append(test4['수입금액(달러)'].iloc[number])
                        new_exim5.append(test4['무역수지(달러)'].iloc[number])
                    except:
                        new_exim1.append(np.nan)
                        new_exim2.append(np.nan)
                        new_exim3.append(np.nan)
                        new_exim4.append(np.nan)
                        new_exim5.append(np.nan)

                df2 = pd.DataFrame()
                df2['수출중량(kg)'] = new_exim1
                df2['수출금액(달러)'] = new_exim2
                df2['수입중량(kg)'] = new_exim3
                df2['수입금액(달러)'] = new_exim4
                df2['무역수지(달러)'] = new_exim5

                globals()[f'df_{cd_number}'] = pd.concat([globals()[f'df_{cd_number}'], df2],axis=1)

            else:
                df2 = pd.DataFrame()
                df2['수출중량(kg)'] = np.nan
                df2['수출금액(달러)'] = np.nan
                df2['수입중량(kg)'] = np.nan
                df2['수입금액(달러)'] = np.nan
                df2['무역수지(달러)'] = np.nan

                globals()[f'df_{cd_number}'] = pd.concat([globals()[f'df_{cd_number}'], df2], axis=1)


            if check != 0:
                if os.path.exists(f'./data') == False:
                    os.mkdir(f'./data')

                if os.path.exists(f'./data/수출입') == False:
                    os.mkdir(f'./data/수출입')

                df2.to_csv(f'./data/수출입/{file_name}', index=False)

    def add_weather(self, check=0):

        """
        check = 중간 산출물을 저장하고 싶다면 check 을 0 이외의 숫자로
        weather 품목별 주산지 데이터를 가져와 합치는 함수, 일부 품목의 주산지가 3개가 아닌 것에 대해서는 np.nan 값으로 합쳐줌
        """

        for i in tqdm(self.pummok):
            name = i.split('_')[-1].split('.')[0]
            check_file = [j for j in self.weather if j.split('_')[-2] == name]


            df = pd.DataFrame()
            for d, j in enumerate(check_file):
                weather_df = pd.read_csv(j)
                new_exim1, new_exim2, new_exim3, new_exim4, new_exim5, new_exim6 = [], [], [], [], [], []


                for k in globals()[f'df_{name}']['datadate']:
                    try:
                        number = list(weather_df['datadate']).index(k)

                        new_exim1.append(weather_df['초기온도(℃)'].iloc[number])
                        new_exim2.append(weather_df['최대온도(℃)'].iloc[number])
                        new_exim3.append(weather_df['최저온도(℃)'].iloc[number])
                        new_exim4.append(weather_df['평균온도(℃)'].iloc[number])
                        new_exim5.append(weather_df['강수량(ml)'].iloc[number])
                        new_exim6.append(weather_df['습도(%)'].iloc[number])
                    except:
                        new_exim1.append(np.nan)
                        new_exim2.append(np.nan)
                        new_exim3.append(np.nan)
                        new_exim4.append(np.nan)
                        new_exim5.append(np.nan)
                        new_exim6.append(np.nan)


                df[f'주산지_{d}_초기온도(℃)'] = new_exim1
                df[f'주산지_{d}_최대온도(℃)'] = new_exim2
                df[f'주산지_{d}_최저온도(℃)'] = new_exim3
                df[f'주산지_{d}_평균온도(℃)'] = new_exim4
                df[f'주산지_{d}_강수량(ml)'] = new_exim5
                df[f'주산지_{d}_습도(%)'] = new_exim6

            if len(check_file) < 3:
                df[f'주산지_2_초기온도(℃)'] = np.nan
                df[f'주산지_2_최대온도(℃)'] = np.nan
                df[f'주산지_2_최저온도(℃)'] = np.nan
                df[f'주산지_2_평균온도(℃)'] = np.nan
                df[f'주산지_2_강수량(ml)'] = np.nan
                df[f'주산지_2_습도(%)'] = np.nan

            globals()[f'df_{name}'] = pd.concat([globals()[f'df_{name}'], df], axis=1)

            if check !=0:
                if os.path.exists(f'./data') == False:
                    os.mkdir(f'./data')

                if os.path.exists(f'./data/주산지') == False:
                    os.mkdir(f'./data/주산지')

                df.to_csv(f'./data/주산지/weather_{name}.csv', index=False)

    def add_categorical(self, out_dir, data_type="train", check=0):

        """
        check = 중간 산출물을 저장하고 싶다면 check 을 0 이외의 숫자로
        일자별 정보를 넣어주는 함수, 월별, 상순, 하순, 중순 을 원핫 인코딩을 통해 데이터로 넣어주는 함수
        모델이 각 행마다의 정보에서 몇월인지 상순인지 하순인지 파악하며 훈련시키기 위한 변수
        """

        for i in tqdm(self.pummok):
            name = i.split('_')[-1].split('.')[0]

            day_set = []
            month_set = []

            for k in globals()[f'df_{name}']['datadate']:
                day = k % 100
                month = k % 10000 // 100

                if day <= 10:
                    day_set.append('초순')
                elif (day > 10) and (day <= 20):
                    day_set.append('중순')
                else:
                    day_set.append('하순')

                month_set.append(f'{month}월')

            globals()[f'df_{name}']['일자구분'] = day_set
            globals()[f'df_{name}']['월구분'] = month_set

            globals()[f'df_{name}'] = pd.get_dummies(globals()[f'df_{name}'], columns=['일자구분', '월구분'])

            if check !=0:
                if os.path.exists(f'./data') == False:
                    os.mkdir(f'./data')

                if data_type != "train":
                    if os.path.exists(f'./data/{data_type}') == False:
                        os.mkdir(f"./data/{data_type}")
                    if os.path.exists(f'./data/{data_type}/{out_dir}') == False:
                        os.mkdir(f'./data/{data_type}/{out_dir}')
                    globals()[f'df_{name}'].to_csv(f'./data/{data_type}/{out_dir}/{data_type}_{name}.csv', index=False)
                else:
                    if os.path.exists(f'./data/{out_dir}') == False:
                        os.mkdir(f'./data/{out_dir}')
                    globals()[f'df_{name}'].to_csv(f'./data/{out_dir}/{data_type}_{name}.csv', index=False)

&nbsp;

## 데이터 다운 및 압축풀기

In [ ]:
%mkdir data
%cd data

/content/data


In [ ]:
!gdown --id 1Vcm2K6XwNyPgZUE-UIlq5rg5kdDtVG_q

/usr/local/lib/python3.7/dist-packages/gdown/cli.py:131: FutureWarning: Option `--id` was deprecated in version 4.3.1 and will be removed in 5.0. You don't need to pass it anymore to use a file ID.
  category=FutureWarning,
Downloading...
From: https://drive.google.com/uc?id=1Vcm2K6XwNyPgZUE-UIlq5rg5kdDtVG_q
To: /content/data/aT_train_raw.zip
100% 184M/184M [00:01<00:00, 163MB/s]


In [ ]:
!gdown --id 1I1dpHtemwzisu9P4ZB-TWUL7-w72L3iO

/usr/local/lib/python3.7/dist-packages/gdown/cli.py:131: FutureWarning: Option `--id` was deprecated in version 4.3.1 and will be removed in 5.0. You don't need to pass it anymore to use a file ID.
  category=FutureWarning,
Downloading...
From: https://drive.google.com/uc?id=1I1dpHtemwzisu9P4ZB-TWUL7-w72L3iO
To: /content/data/aT_test_raw.zip
100% 16.1M/16.1M [00:00<00:00, 41.3MB/s]


- 정답 제출양식

In [ ]:
!gdown --id 1bXFp41evVZ98CpPPI2f9pLdmqo9Wixef

/usr/local/lib/python3.7/dist-packages/gdown/cli.py:131: FutureWarning: Option `--id` was deprecated in version 4.3.1 and will be removed in 5.0. You don't need to pass it anymore to use a file ID.
  category=FutureWarning,
Downloading...
From: https://drive.google.com/uc?id=1bXFp41evVZ98CpPPI2f9pLdmqo9Wixef
To: /content/data/answer_example.csv
100% 21.7k/21.7k [00:00<00:00, 36.2MB/s]


In [ ]:
!unzip -qq  "/content/data/aT_test_raw.zip"
!unzip -qq  "/content/data/aT_train_raw.zip"

&nbsp;

## 훈련 데이터 전처리 및 저장 (중간저장 X, 최종저장 O) - train

In [ ]:
data = preprocessing_data('./aT_train_raw/*.csv')
data.add_pummock()
data.add_dosomae()
data.add_dosomae(option=2)
data.add_imexport()
data.add_weather()
data.add_categorical('train', data_type="train" ,check=1)

100%|██████████| 37/37 [00:01<00:00, 23.39it/s]


&nbsp;

## 검증 데이터셋 전처리 및 저장 (중간저장 X, 최종저장 O) - test

In [ ]:
for i in range(10):
    data = preprocessing_data(f'./aT_test_raw/sep_{i}/*.csv')
    data.add_pummock()
    data.add_dosomae()
    data.add_dosomae(option=2)
    data.add_imexport()
    data.add_weather()
    data.add_categorical(f'set_{i}', data_type="test", check=1)

100%|██████████| 37/37 [00:00<00:00, 208.74it/s]


&nbsp;

## 입력 shape 및 형태 정의 함수

In [3]:
def make_Tensor(array):
    return tf.convert_to_tensor(array, dtype=tf.float32)

def astype_data(data):
    df = data.astype(np.float32)
    return make_Tensor(df)

&nbsp;

## Transformer 정의

- encoder

In [4]:
def transformer_encoder(inputs, head_size, num_heads, ff_dim, dropout=0):

    x = layers.LayerNormalization(epsilon=1e-6)(inputs)
    x = layers.MultiHeadAttention(
        key_dim=head_size, num_heads=num_heads, dropout=dropout
    )(x, x)
    x = layers.Dropout(dropout)(x)
    res = x + inputs

    x = layers.LayerNormalization(epsilon=1e-6)(res)
    x = layers.Conv1D(filters=ff_dim, kernel_size=1, activation="relu")(x)
    x = layers.Dropout(dropout)(x)
    x = layers.Conv1D(filters=inputs.shape[-1], kernel_size=1)(x)
    return x + res

- build

In [5]:
def build_model(input_shape, head_size, num_heads, ff_dim, num_transformer_blocks, mlp_units, dropout=0, mlp_dropout=0):
    inputs = keras.Input(shape=input_shape)
    x = inputs
    for _ in range(num_transformer_blocks):
        x = transformer_encoder(x, head_size, num_heads, ff_dim, dropout)

    x = layers.GlobalAveragePooling1D(data_format="channels_first")(x)
    for dim in mlp_units:
        x = layers.Dense(dim, activation="relu")(x)
        x = layers.Dropout(mlp_dropout)(x)
    outputs = layers.Dense(28)(x) # 4주 예측
    return keras.Model(inputs, outputs)

&nbsp;

## keras eraly stop, chekpoint 정의

In [6]:
def call_back_set(name, epoch, batch_size):
    early_stopping = EarlyStopping(monitor='val_loss', patience=50)

    if os.path.exists(f'./check') == False:
        os.mkdir(f'./check')

    filename = f'./check/{name}-{epoch}-{batch_size}.h5'

    checkpoint = ModelCheckpoint(filename,
                                 monitor='val_loss',
                                 verbose=1,
                                 save_best_only=True,
                                 save_weights_only=True,
                                 mode='auto'
                                 )
    return [early_stopping, checkpoint]

&nbsp;

## Model 훈련 함수

In [7]:
def train(x_train, y_train, x_val, y_val, name, epoch, batch_size, learning_rate = 0.001, verbose = 1):


    model = build_model(
    x_train.shape[1:],
    head_size=256,
    num_heads=4,
    ff_dim=4,
    num_transformer_blocks=4,
    mlp_units=[128],
    mlp_dropout=0.4,
    dropout=0.25,
    )

    model.compile(
        loss="mean_squared_error",
        optimizer=keras.optimizers.Adam(learning_rate=learning_rate)
    )


    # Train the model
    with tf.device('/device:GPU:0'):
        history1 = model.fit(
            x_train, y_train,
            epochs = epoch,
            steps_per_epoch=len(x_train) / batch_size,
            batch_size=batch_size,
            validation_data=(x_val, y_val),
            validation_steps=len(x_val) / batch_size,
            shuffle=False,
            callbacks=call_back_set(name, epoch, batch_size),
            verbose=verbose)

    return model

&nbsp;

## 시점 윈도우 생성 함수

In [8]:
def time_window(df, t, t_sep):
    seq_len = t
    seqence_length = seq_len + t_sep

    result = []
    for index in tqdm(range(len(df) - seqence_length)):
        result.append(df[index: index + seqence_length].values)

    return np.array(result)

&nbsp;

## 데이터 불러오기 및 parameter 설정

In [9]:
data_list = glob('./data//train/*.csv')
epoch = 1000 # default: 1000
batch = 15 # default: 15
# tr_del_list = ['단가(원)', '거래량', '거래대금(원)', '경매건수', '도매시장코드', '도매법인코드', '산지코드 '] # train 에서 사용하지 않는 열
# ts_del_list = ['단가(원)', '거래량', '거래대금(원)', '경매건수', '도매시장코드', '도매법인코드', '산지코드 ', '해당일자_전체평균가격(원)'] # test 에서 사용하지 않는 열
tr_del_list = ['단가(원)', '거래량', '거래대금(원)', '경매건수', '도매시장코드', '도매법인코드', '산지코드 ', '해당일자_전체거래물량(kg)'] # train 에서 사용하지 않는 열
ts_del_list = ['단가(원)', '거래량', '거래대금(원)', '경매건수', '도매시장코드', '도매법인코드', '산지코드 ', '해당일자_전체거래물량(kg)', '해당일자_전체평균가격(원)'] # test 에서 사용하지 않는 열
check_col = ['일자구분_중순', '일자구분_초순', '일자구분_하순','월구분_10월', '월구분_11월', '월구분_12월', '월구분_1월', '월구분_2월', '월구분_3월', 
             '월구분_4월','월구분_5월', '월구분_6월', '월구분_7월', '월구분_8월', '월구분_9월'] # 열 개수 맞추기

&nbsp;

## Train 과정

In [10]:
i = data_list[0]

df_number = i.split("_")[-1].split(".")[0]
df = pd.read_csv(i)

for j in df.columns:
    df[j] = df[j].replace({' ': np.nan})

# 사용할 열 선택 및 index 설정
df.drop(tr_del_list, axis=1, inplace=True)
df.set_index('datadate', drop=True, inplace=True)

# nan 처리
df = df.fillna(0)

# 변수와 타겟 분리
x, y = df[[i for i in df.columns if i != '해당일자_전체평균가격(원)']], df['해당일자_전체평균가격(원)']

# 2주 입력을 통한 이후 4주 예측을 위해 y의 첫 14일을 제외
y = y[14:]

# time series window 생성
data_x = time_window(x, 13, 1)
data_y = time_window(y, 27, 1)

# y의 길이와 같은 길이로 설정
xdata = data_x[:len(data_y)]
ydata = data_y

100%|██████████| 1419/1419 [00:00<00:00, 32557.92it/s]


In [12]:
data_x

array([[[0.0, 0.0, 0.0, ..., 0, 0, 0],
        [1459.61691834643, 2026.0139518281055, 29270.0, ..., 0, 0, 0],
        [1722.9341704128817, 2222.779560453201, 202649.0, ..., 0, 0, 0],
        ...,
        [1506.9663128088478, 2087.3576755044483, 127490.0, ..., 0, 0, 0],
        [1443.8896626204926, 2102.58472440556, 112040.0, ..., 0, 0, 0],
        [1464.8613209095736, 2113.799721471192, 103565.0, ..., 0, 0, 0]],

       [[1459.61691834643, 2026.0139518281055, 29270.0, ..., 0, 0, 0],
        [1722.9341704128817, 2222.779560453201, 202649.0, ..., 0, 0, 0],
        [1614.6376831423895, 2172.903839585046, 152750.0, ..., 0, 0, 0],
        ...,
        [1443.8896626204926, 2102.58472440556, 112040.0, ..., 0, 0, 0],
        [1464.8613209095736, 2113.799721471192, 103565.0, ..., 0, 0, 0],
        [0.0, 0.0, 0.0, ..., 0, 0, 0]],

       [[1722.9341704128817, 2222.779560453201, 202649.0, ..., 0, 0, 0],
        [1614.6376831423895, 2172.903839585046, 152750.0, ..., 0, 0, 0],
        [1597.4248662

In [18]:
for i in tqdm(data_list):
    df_number = i.split("_")[-1].split(".")[0]
    df = pd.read_csv(i)

    for j in df.columns:
        df[j] = df[j].replace({' ': np.nan})

    # 사용할 열 선택 및 index 설정
    df.drop(tr_del_list, axis=1, inplace=True)
    df.set_index('datadate', drop=True, inplace=True)

    # nan 처리
    df = df.fillna(0)

    # 변수와 타겟 분리
    x, y = df[[i for i in df.columns if i != '해당일자_전체평균가격(원)']], df['해당일자_전체평균가격(원)']

    # 2주 입력을 통한 이후 4주 예측을 위해 y의 첫 14일을 제외
    y = y[14:]

    # time series window 생성
    data_x = time_window(x, 13, 1)
    data_y = time_window(y, 27, 1)

    # y의 길이와 같은 길이로 설정
    xdata = data_x[:len(data_y)]
    ydata = data_y

    # train, validation 분리 (8 : 2)
    x_train, x_val, y_train, y_val = train_test_split(xdata, ydata, test_size=0.2, shuffle=False, random_state=119)

    # transformer 모델 훈련
    transformer = train(astype_data(x_train), y_train, astype_data(x_val), y_val, f'transformer-{df_number}', epoch,
                        batch)
    transformer.load_weights(f'./check/transformer-{df_number}-{epoch}-{batch}.h5')

    if os.path.exists(f'./model') == False:
        os.mkdir(f'./model')

    # 모델 저장
    transformer.save(f'./model/transformer-{df_number}-{epoch}-{batch}.h5')

100%|██████████| 1419/1419 [00:00<00:00, 29742.38it/s]


Epoch 1/1000


2022-09-02 13:27:39.280128: I tensorflow/stream_executor/cuda/cuda_dnn.cc:384] Loaded cuDNN version 8302
2022-09-02 13:27:41.018899: I tensorflow/core/platform/default/subprocess.cc:304] Start cannot spawn child process: 그런 파일이나 디렉터리가 없습니다


76/75 [==============================] - ETA: 0s - loss: 407583008.0000
Epoch 1: val_loss improved from inf to 45447448.00000, saving model to ./check/transformer-7-1000-15.h5
75/75 [==============================] - 10s 29ms/step - loss: 407583008.0000 - val_loss: 45447448.0000
Epoch 2/1000
74/75 [============================>.] - ETA: 0s - loss: 174736528.0000
Epoch 2: val_loss improved from 45447448.00000 to 24799254.00000, saving model to ./check/transformer-7-1000-15.h5
75/75 [==============================] - 2s 23ms/step - loss: 172444960.0000 - val_loss: 24799254.0000
Epoch 3/1000
76/75 [==============================] - ETA: 0s - loss: 98415400.0000 
Epoch 3: val_loss improved from 24799254.00000 to 16541617.00000, saving model to ./check/transformer-7-1000-15.h5
75/75 [==============================] - 2s 23ms/step - loss: 98415400.0000 - val_loss: 16541617.0000
Epoch 4/1000
76/75 [==============================] - ETA: 0s - loss: 59681176.0000
Epoch 4: val_loss improved from

100%|██████████| 1419/1419 [00:00<00:00, 28412.41it/s]


...

100%|██████████| 1419/1419 [00:00<00:00, 28965.23it/s]


Epoch 1/1000
74/75 [============================>.] - ETA: 0s - loss: 590214272.0000
Epoch 1: val_loss improved from inf to 87828800.00000, saving model to ./check/transformer-33-1000-15.h5
75/75 [==============================] - 7s 29ms/step - loss: 579316096.0000 - val_loss: 87828800.0000
Epoch 2/1000
74/75 [============================>.] - ETA: 0s - loss: 334812832.0000
Epoch 2: val_loss improved from 87828800.00000 to 68239264.00000, saving model to ./check/transformer-33-1000-15.h5
75/75 [==============================] - 2s 22ms/step - loss: 328761856.0000 - val_loss: 68239264.0000
Epoch 3/1000
76/75 [==============================] - ETA: 0s - loss: 249921392.0000
Epoch 3: val_loss improved from 68239264.00000 to 60127672.00000, saving model to ./check/transformer-33-1000-15.h5
75/75 [==============================] - 2s 24ms/step - loss: 249921392.0000 - val_loss: 60127672.0000
Epoch 4/1000
76/75 [==============================] - ETA: 0s - loss: 200285184.0000
Epoch 4: val_l

100%|██████████| 1419/1419 [00:00<00:00, 27381.09it/s]


Epoch 1/1000
76/75 [==============================] - ETA: 0s - loss: 3991788032.0000
Epoch 1: val_loss improved from inf to 939883456.00000, saving model to ./check/transformer-15-1000-15.h5
75/75 [==============================] - 6s 31ms/step - loss: 3991788032.0000 - val_loss: 939883456.0000
Epoch 2/1000
76/75 [==============================] - ETA: 0s - loss: 1414952320.0000
Epoch 2: val_loss improved from 939883456.00000 to 430757504.00000, saving model to ./check/transformer-15-1000-15.h5
75/75 [==============================] - 2s 24ms/step - loss: 1414952320.0000 - val_loss: 430757504.0000
Epoch 3/1000
76/75 [==============================] - ETA: 0s - loss: 660804544.0000
Epoch 3: val_loss improved from 430757504.00000 to 262154960.00000, saving model to ./check/transformer-15-1000-15.h5
75/75 [==============================] - 2s 23ms/step - loss: 660804544.0000 - val_loss: 262154960.0000
Epoch 4/1000
76/75 [==============================] - ETA: 0s - loss: 384285984.0000
Ep

100%|██████████| 37/37 [9:51:08<00:00, 958.60s/it]


&nbsp;

## Test 과정

In [13]:
zero_csv = [0 for i in range(14)]  # 시점이 비어있는 데이터 0으로 채우기 위한 변수

for i in tqdm(range(10)):
    data_list = glob(f'./data/test/set_{i}/*.csv')

    for idx,j in enumerate(data_list):
        df = pd.read_csv(j)

        if len(df) == 0:
            df['zero_non'] = zero_csv
            df = df.fillna(0)
            df.drop('zero_non', axis=1, inplace=True)


        file_number = j.split('test_')[1].split('.')[0]

        # 사용할 열 선택, index 설정
        df.drop(ts_del_list, axis=1, inplace=True)
        df.set_index('datadate', drop=True, inplace=True)

        # train input 과 형상 맞추기
        add_col = [i for i in check_col if i not in df.columns]

        for a in add_col:
            df[a] = 0

        # ' ' -> nan 으로 변경
        for a in df.columns:
            df[a] = df[a].replace({' ': np.nan})

        # nan 처리
        df = df.fillna(0)

        # x_test  생성
        df_test = astype_data(df.values.reshape(1, df.values.shape[0], df.values.shape[1]))


        # model test
        if os.path.exists(f'./model_output_{epoch}_{batch}') == False:
            os.mkdir(f'./model_output_{epoch}_{batch}')

        if os.path.exists(f'./model_output_{epoch}_{batch}/set_{i}') == False:
            os.mkdir(f'./model_output_{epoch}_{batch}/set_{i}')

        # 해당하는 모델 불러오기
        transformer = tf.keras.models.load_model(f'./model/transformer-{file_number}-{epoch}-{batch}.h5') # model_test
        pred = transformer.predict(df_test)


        # 결과 저장
        save_df = pd.DataFrame(pred).T
        save_df.to_csv(f'./model_output_{epoch}_{batch}/set_{i}/predict_{file_number}.csv', index=False)

  0%|          | 0/10 [00:00<?, ?it/s]

1/1 [==============================] - 0s 343ms/step


 10%|█         | 1/10 [00:35<05:22, 35.86s/it]

1/1 [==============================] - 0s 353ms/step


 20%|██        | 2/10 [01:11<04:46, 35.81s/it]

...

 80%|████████  | 8/10 [04:47<01:11, 35.99s/it]

1/1 [==============================] - 0s 327ms/step


 90%|█████████ | 9/10 [05:23<00:36, 36.02s/it]

1/1 [==============================] - 0s 355ms/step


100%|██████████| 10/10 [05:59<00:00, 35.94s/it]


In [14]:
file_number

'29'

&nbsp;

## 정답 제출 파일생성

In [18]:
for k in tqdm(range(10)):

  globals()[f'set_df_{k}'] = pd.DataFrame()
  answer_df_list = glob(f'./model_output_{epoch}_{batch}/set_{k}/*.csv') # 예측한 결과 불러오기
  pum_list = glob(f'./aT_test_raw/sep_{k}/*.csv') # 기존 test input 불러오기
  pummok = [a for a in pum_list if 'pummok' in a.split('/')[-1]]

  for i in answer_df_list:
    df = pd.read_csv(i)
    number = i.split('_')[-1].split('.')[0]

    base_number = 0
    for p in pummok:
      if number == p.split('_')[-1].split('.')[0]:
        pum_df = pd.read_csv(p)

        if len(pum_df) != 0:
           base_number = pum_df.iloc[len(pum_df)-1]['해당일자_전체평균가격(원)']  # 기존 각 sep 마다 test input의 마지막 target 값 가져오기 (변동률 계산을 위해)
        else:
          base_number = np.nan

    globals()[f'set_df_{k}'][f'품목{number}']  = [base_number] + list(df[df.columns[-1]].values) # 각 품목당 순서를 t, t+1 ... t+28 로 변경

  globals()[f'set_df_{k}'] = globals()[f'set_df_{k}'][[f'품목{col}' for col in range(37)]] # 열 순서를 품목0 ~ 품목36 으로 변경

100%|██████████| 10/10 [00:02<00:00,  4.52it/s]


- 변동률 계산을 위한 t, t+1 ... t+28 설정

In [19]:
set_df_0

품목0          품목1           품목2          품목3          품목4  \
0   3871.1250  1362.117613   2909.783785  3400.075583  3947.809169   
1   3779.8489    63.662865   7879.261000    25.271600    69.016170   
2   3818.6300    63.686436   2394.202600    24.845182    69.242820   
3   3776.0613    64.051100   1148.875000    25.333166    68.113525   
4   3821.6946    63.867332  -1548.090700    24.659760    69.024200   
5   3712.1826    63.739986  -9774.257000    25.360546    68.876250   
6   3810.4531    64.047200   2590.975300    25.401667    69.294334   
7   3825.2510    64.286310  14828.982000    23.861969    68.561380   
8   3774.5667    64.152170  -6444.304000    24.664932    68.220270   
9   3807.5713    63.929340   2770.253700    25.240190    68.710200   
10  3744.4539    63.919098  -5809.992700    25.577394    68.796210   
11  3824.7898    63.651530   9267.343000    25.479338    68.102570   
12  3708.4521    64.066284  -5969.790500    25.649721    69.419070   
13  3826.2065    63.739243   1084.905600    25.728664    68.124850   
14  3855.3408    64.234710  10119.987000    25.736994    69.195880   
15  3783.3652    64.553780    334.249400    25.374495    67.449080   
16  3842.5620    64.316750   -193.284010    25.333520    68.706810   
17  3831.2078    63.768093   -859.048600    25.470848    68.489624   
18  3834.2292    64.230050  10147.119000    25.105011    69.070010   
19  3734.9697    64.194770   8642.417000    24.830460    69.209290   
20  3848.7239    63.953495  -4340.704600    25.755442    68.385870   
21  3877.9316    64.141090  -6148.900400    25.669094    69.279396   
22  3785.8638    64.212234   8959.256000    25.457455    68.359720   
23  3832.5298    63.856846  -7046.363300    24.815810    68.775860   
24  3778.9820    64.163760   5041.168000    24.622034    68.901970   
25  3844.2083    64.047150   4417.009000    25.281116    68.786736   
26  3764.7266    63.770523   6853.138700    23.946700    69.456970   
27  3850.5466    64.164440  -8252.169000    25.554287    69.389084   
28  3881.7842    63.774860  -3851.838600    25.395105    68.883700   

            품목5          품목6          품목7          품목8          품목9  ...  \
0   9253.947514  2717.280000  3361.030923  4911.899864  1173.018633  ...   
1   3751.231400    52.502174  1161.637600     0.611764     0.626832  ...   
2   3751.848400    53.288420  1207.428300     0.445116     0.689319  ...   
3   3773.274700    52.363983  1188.504600     0.551247     0.288688  ...   
4   3818.697500    52.341084  1170.656900     0.372180     0.928797  ...   
5   3877.419400    52.498540  1166.122600     0.528700     1.073576  ...   
6   3744.872600    52.332840  1204.163700     0.456592     0.593231  ...   
7   3862.844200    52.810856  1201.433000     0.388878     0.843518  ...   
8   3898.401000    52.816540  1149.774000     0.609717     0.979607  ...   
9   3854.892300    53.360440  1215.082600     0.507825     0.903117  ...   
10  3974.276600    52.963894  1186.549700     0.651776     0.685564  ...   
11  3990.145500    52.673340  1170.801400     0.573255     0.889799  ...   
12  3908.883300    52.569347  1208.541700     0.477355     0.426926  ...   
13  3768.852500    52.229530  1201.189800     0.584199     0.625284  ...   
14  4024.930400    51.507840  1189.781500     0.530518     0.492533  ...   
15  4022.849400    51.721770  1142.775800     0.494420     0.976946  ...   
16  3852.490000    52.740795  1208.639300     0.472851     0.535600  ...   
17  3923.196000    53.278500  1197.787500     0.466661     0.645472  ...   
18  4062.741700    52.696495  1230.387800     0.569468     0.283223  ...   
19  4021.176000    52.460915  1194.194300     0.545601     0.737395  ...   
20  3877.953000    52.769090  1231.639600     0.571597     0.925337  ...   
21  4003.962400    52.750060  1237.470100     0.505824     1.052885  ...   
22  4092.392300    53.091034  1200.301900     0.398699     0.864084  ...   
23  3961.216600    53.262280  1250.408300     0.497765     0.467132  ...   
24  3968.

- 변동률 계산 

In [20]:
date = [f'd+{i}' for i in range(1,15)] + ['d+22 ~ 28 평균']


for k in range(10):
  globals()[f'answer_df_{k}'] = pd.DataFrame()
  for c in globals()[f'set_df_{k}'].columns:
    base_d = globals()[f'set_df_{k}'][c][0] # 변동률 기준 t 값

    ans_1_14 = []
    for i in range(14):
      ans_1_14.append((globals()[f'set_df_{k}'][c].iloc[i+1]- base_d)/base_d)  # t+1 ~ t+14 까지는 (t+n - t)/t 로 계산

    ans_22_28 = (globals()[f'set_df_{k}'][c][22:29].mean() - base_d)/base_d # t+22 ~ t+28은 np.mean(t+22 ~ t+28) - t / t

    globals()[f'answer_df_{k}'][f'{c} 변동률'] = ans_1_14 + [ans_22_28]
  
  globals()[f'answer_df_{k}']['Set'] = k # set 번호 설정
  globals()[f'answer_df_{k}']['일자'] = date # 일자 설정

- sep 0  ~ sep 9 까지 합치기

In [21]:
# 위에서 계산된 변동률 들을 합쳐주는 과정

all_df =pd.DataFrame()
for i in range(10):
  if i== 0 :
    all_df = pd.concat([all_df, globals()[f'answer_df_{i}']],axis=1)
  else:
    all_df = pd.concat([all_df, globals()[f'answer_df_{i}']])


all_df = all_df[['Set','일자'] + list(all_df.columns[:-2])]
all_df.reset_index(drop=True, inplace=True)

- 정답 양식으로 변경

In [22]:
# set, 일자 기억하기위해 따로 저장

re_set = list(all_df['Set'])
re_date = list(all_df['일자'])


# 정답 양식 불러오기
out_ans = pd.read_csv('./answer_example.csv')

# 두 dataframe 합치기 (nan + 숫자 = nan 이용)
submit_df = all_df + out_ans

submit_df['Set'] = re_set
submit_df['일자'] = re_date


# 최종 저장
submit_df.to_csv('./submit.csv',index=False)

- 계산된 변동률 결과물

In [23]:
all_df

Set            일자   품목0 변동률   품목1 변동률   품목2 변동률   품목3 변동률   품목4 변동률  \
0      0           d+1 -0.023579 -0.953262  1.707851 -0.992567 -0.982518   
1      0           d+2 -0.013561 -0.953245 -0.177189 -0.992693 -0.982460   
2      0           d+3 -0.024557 -0.952977 -0.605168 -0.992549 -0.982747   
3      0           d+4 -0.012769 -0.953112 -1.532029 -0.992747 -0.982516   
4      0           d+5 -0.041058 -0.953205 -4.359101 -0.992541 -0.982553   
..   ...           ...       ...       ...       ...       ...       ...   
145    9          d+11 -0.504086 -0.956117 -0.323331 -0.990031 -0.980033   
146    9          d+12 -0.517992 -0.955831 -0.268233 -0.989964 -0.979647   
147    9          d+13 -0.500316 -0.956057 -0.327556 -0.989933 -0.980026   
148    9          d+14 -0.496411 -0.955715 -0.293712 -0.989930 -0.979712   
149    9  d+22 ~ 28 평균 -0.502725 -0.955878 -0.307688 -0.990214 -0.979788   

      품목5 변동률   품목6 변동률   품목7 변동률  ...  품목27 변동률  품목28 변동률  품목29 변동률  \
0   -0.594634 -0.980678 -0.654381  ... -0.504933 -0.893527 -0.937273   
1   -0.594568 -0.980389 -0.640757  ... -0.494893 -0.893140 -0.936529   
2   -0.592252 -0.980729 -0.646387  ... -0.503441 -0.893611 -0.935658   
3   -0.587344 -0.980738 -0.651697  ... -0.497522 -0.893750 -0.935778   
4   -0.580998 -0.980680 -0.653046  ... -0.498706 -0.893732 -0.935417   
..        ...       ...       ...  ...       ...       ...       ...   
145 -0.262170 -0.991752       NaN  ... -0.159612 -0.890651 -0.942598   
146 -0.277172 -0.991768       NaN  ... -0.173959 -0.890625 -0.942582   
147 -0.303042 -0.991821       NaN  ... -0.182470 -0.890653 -0.942303   
148 -0.255727 -0.991934       NaN  ... -0.204499 -0.890344 -0.942682   
149 -0.252594 -0.991686       NaN  ... -0.174474 -0.890801 -0.942649   

     품목30 변동률  품목31 변동률  품목32 변동률  품목33 변동률  품목34 변동률  품목35 변동률  품목36 변동률  
0   -0.958103 -0.999902 -1.122326 -0.135251 -0.986722 -0.449366 -0.348936  
1   -0.958240 -0.999885 -0.528166 -0.120410 -0.986694 -0.451079 -0.356503  
2   -0.957277 -0.999876 -0.921015 -0.126996 -0.986719 -0.446036 -0.358639  
3   -0.957787 -0.999898 -1.353308 -0.132725 -0.986769 -0.449946 -0.332282  
4   -0.957492 -0.999865 -0.723418 -0.135249 -0.986714 -0.455086 -0.385871  
..        ...       ...       ...       ...       ...       ...       ...  
145 -0.933676 -0.999849 -0.999926 -0.434073 -0.967739 -0.040622 -0.385851  
146 -0.933279 -0.999812 -0.999924 -0.430939 -0.967076 -0.053099 -0.456739  
147 -0.932614 -0.999868 -0.999912 -0.455826 -0.967144 -0.043490 -0.414601  
148 -0.932998 -0.999877 -0.999919 -0.440571 -0.967398 -0.058574 -0.409218  
149 -0.933303 -0.999863 -0.999940 -0.460689 -0.967346 -0.049621 -0.428486  

[150 rows x 39 columns]

- 제출 양식

In [24]:
out_ans

Set            일자  품목0 변동률  품목1 변동률  품목2 변동률  품목3 변동률  품목4 변동률  품목5 변동률  \
0      0           d+1      0.0      0.0      0.0      0.0      0.0      0.0   
1      0           d+2      0.0      0.0      0.0      0.0      0.0      0.0   
2      0           d+3      NaN      NaN      NaN      NaN      NaN      NaN   
3      0           d+4      0.0      0.0      0.0      0.0      0.0      0.0   
4      0           d+5      0.0      0.0      0.0      0.0      0.0      0.0   
..   ...           ...      ...      ...      ...      ...      ...      ...   
145    9          d+11      0.0      0.0      0.0      0.0      0.0      0.0   
146    9          d+12      0.0      0.0      0.0      0.0      0.0      0.0   
147    9          d+13      0.0      0.0      0.0      0.0      0.0      0.0   
148    9          d+14      0.0      0.0      0.0      0.0      0.0      0.0   
149    9  d+22 ~ 28 평균      0.0      0.0      0.0      0.0      0.0      0.0   

     품목6 변동률  품목7 변동률  ...  품목27 변동률  품목28 변동률  품목29 변동률  품목30 변동률  품목31 변동률  \
0        0.0      0.0  ...       0.0       0.0       0.0       0.0       0.0   
1        NaN      0.0  ...       0.0       0.0       0.0       0.0       0.0   
2        0.0      NaN  ...       NaN       NaN       NaN       NaN       NaN   
3        NaN      0.0  ...       0.0       0.0       0.0       0.0       0.0   
4        NaN      0.0  ...       0.0       0.0       0.0       0.0       0.0   
..       ...      ...  ...       ...       ...       ...       ...       ...   
145      0.0      NaN  ...       0.0       0.0       0.0       0.0       0.0   
146      0.0      NaN  ...       0.0       0.0       0.0       0.0       0.0   
147      0.0      NaN  ...       0.0       0.0       0.0       0.0       0.0   
148      0.0      NaN  ...       0.0       0.0       0.0       0.0       0.0   
149      NaN      NaN  ...       0.0       0.0       0.0       0.0       0.0   

     품목32 변동률  품목33 변동률  품목34 변동률  품목35 변동률  품목36 변동률  
0         0.0       0.0       0.0       0.0       0.0  
1         0.0       0.0       0.0       0.0       0.0  
2         NaN       NaN       NaN       NaN       NaN  
3         0.0       0.0       0.0       0.0       0.0  
4         0.0       0.0       0.0       0.0       0.0  
..        ...       ...       ...       ...       ...  
145       0.0       0.0       0.0       0.0       0.0  
146       0.0       0.0       0.0       0.0       0.0  
147       0.0       0.0       0.0       0.0       0.0  
148       0.0       0.0       0.0       0.0       0.0  
149       0.0       0.0       0.0       0.0       0.0  

[150 rows x 39 columns]

- 제출 양식 반영한 최종 결과물 (**실 제출용**)

In [25]:
submit_df

Set            일자   품목0 변동률   품목1 변동률   품목2 변동률   품목3 변동률   품목4 변동률  \
0      0           d+1 -0.023579 -0.953262  1.707851 -0.992567 -0.982518   
1      0           d+2 -0.013561 -0.953245 -0.177189 -0.992693 -0.982460   
2      0           d+3       NaN       NaN       NaN       NaN       NaN   
3      0           d+4 -0.012769 -0.953112 -1.532029 -0.992747 -0.982516   
4      0           d+5 -0.041058 -0.953205 -4.359101 -0.992541 -0.982553   
..   ...           ...       ...       ...       ...       ...       ...   
145    9          d+11 -0.504086 -0.956117 -0.323331 -0.990031 -0.980033   
146    9          d+12 -0.517992 -0.955831 -0.268233 -0.989964 -0.979647   
147    9          d+13 -0.500316 -0.956057 -0.327556 -0.989933 -0.980026   
148    9          d+14 -0.496411 -0.955715 -0.293712 -0.989930 -0.979712   
149    9  d+22 ~ 28 평균 -0.502725 -0.955878 -0.307688 -0.990214 -0.979788   

      품목5 변동률   품목6 변동률   품목7 변동률  ...  품목27 변동률  품목28 변동률  품목29 변동률  \
0   -0.594634 -0.980678 -0.654381  ... -0.504933 -0.893527 -0.937273   
1   -0.594568       NaN -0.640757  ... -0.494893 -0.893140 -0.936529   
2         NaN -0.980729       NaN  ...       NaN       NaN       NaN   
3   -0.587344       NaN -0.651697  ... -0.497522 -0.893750 -0.935778   
4   -0.580998       NaN -0.653046  ... -0.498706 -0.893732 -0.935417   
..        ...       ...       ...  ...       ...       ...       ...   
145 -0.262170 -0.991752       NaN  ... -0.159612 -0.890651 -0.942598   
146 -0.277172 -0.991768       NaN  ... -0.173959 -0.890625 -0.942582   
147 -0.303042 -0.991821       NaN  ... -0.182470 -0.890653 -0.942303   
148 -0.255727 -0.991934       NaN  ... -0.204499 -0.890344 -0.942682   
149 -0.252594       NaN       NaN  ... -0.174474 -0.890801 -0.942649   

     품목30 변동률  품목31 변동률  품목32 변동률  품목33 변동률  품목34 변동률  품목35 변동률  품목36 변동률  
0   -0.958103 -0.999902 -1.122326 -0.135251 -0.986722 -0.449366 -0.348936  
1   -0.958240 -0.999885 -0.528166 -0.120410 -0.986694 -0.451079 -0.356503  
2         NaN       NaN       NaN       NaN       NaN       NaN       NaN  
3   -0.957787 -0.999898 -1.353308 -0.132725 -0.986769 -0.449946 -0.332282  
4   -0.957492 -0.999865 -0.723418 -0.135249 -0.986714 -0.455086 -0.385871  
..        ...       ...       ...       ...       ...       ...       ...  
145 -0.933676 -0.999849 -0.999926 -0.434073 -0.967739 -0.040622 -0.385851  
146 -0.933279 -0.999812 -0.999924 -0.430939 -0.967076 -0.053099 -0.456739  
147 -0.932614 -0.999868 -0.999912 -0.455826 -0.967144 -0.043490 -0.414601  
148 -0.932998 -0.999877 -0.999919 -0.440571 -0.967398 -0.058574 -0.409218  
149 -0.933303 -0.999863 -0.999940 -0.460689 -0.967346 -0.049621 -0.428486  

[150 rows x 39 columns]

In [26]:
# model_sample = tf.keras.models.load_model('model/transformer-3-1000-15.h5')
# model_sample.summary()